# **\[SOLAR\]** SIMULATION (TGCN)

JiyunLim  
2020-12-22

## Data

In [1]:
import pandas as pd
import numpy as np
import os

In [2]:
# read dataframe 
df = pd.read_csv('data_eng_230710.csv')

# make y, y_upper, y_period, time, regions 
y = df.loc[:,'Bukchoncheon':'Gyeongju-si'].to_numpy()
yU = df.loc[:,'Bukchoncheon_Upper':'Gyeongju-si_Upper'].to_numpy()
yP = np.divide(y, yU+1e-10)
t = df.loc[:,'date']
regions = list(df.loc[:,'Bukchoncheon':'Gyeongju-si'].columns)

TRAIN_RATIO = 0.8
T,N = len(t),len(regions) 
LEN_TEST = int(np.floor(T*(1-TRAIN_RATIO)))
LEN_TR = T - LEN_TEST

## TGCN

In [3]:
%run model/tgcn

In [4]:
s5 = Simulator()

In [5]:
class T_GCN(torch.nn.Module):
    def __init__(self, node_features, filters):
        super(T_GCN, self).__init__()
        self.recurrent = TGCN(node_features, filters)
        self.linear = torch.nn.Linear(filters, 1)

    def forward(self, x, edge_index, edge_weight, prev_hidden_state):
        h = self.recurrent(x, edge_index, edge_weight, prev_hidden_state)
        y = F.relu(h)
        y = self.linear(y)
        return y, h

In [6]:
s5.simulate(
    n_iteration = 30,
    lags = [4, 8, 12],
    filters = [4, 8, 16, 32],
    epoch = [50],
    Model = T_GCN
)

5/50

In [ ]:
fnames = ['./results/'+l for l in os.listdir('./results/') if l[0] != '.']
fnames 

## RSLT

In [ ]:
df_ = pd.concat([pd.read_csv(fname) for fname in fnames]).reset_index(drop=True)

In [ ]:
df_

In [ ]:
df_.groupby(by=['model','method']).agg({'mse':[np.mean, np.std]})